In [1]:
import random
from IPython.core.display import SVG
import pyomo.environ as pyo
from pysat.solvers import Solver
from pysat.formula import CNF 
import py_svg_combinatorics as psc
from ipywidgets import widgets, HBox
from collections import Counter
from pprint import pprint
from random import randint
import numpy as np
from IPython.display import IFrame
import IPython
from copy import copy
import os
from pathlib import Path
np.set_printoptions(precision=2)
np.set_printoptions(suppress=True)
nbname = ''
try:
    nbname = __vsc_ipynb_file__
except:
    if 'COCALC_JUPYTER_FILENAME' in os.environ:
        nbname = os.environ['COCALC_JUPYTER_FILENAME']    
title_ = Path(nbname).stem.replace('-', '_').title()    
IFrame(f'https://discopal.ispras.ru/index.php?title=Hardprob/{title_}&useskin=cleanmonobook', width=1280, height=300)

In [2]:
# Случайные данные
m = np.random.randint(3, 20)
n = np.random.randint(3, 20)
A = np.random.rand(m, n)
c = np.random.rand(n)
b = 1/np.random.rand(m)
# Модифицируем тестовые данные, чтобы получались только задачи имеющие решение.
for i in range(len(b)):
    b[i] = min(b[i], sum(A[i, j] for j in range(n)))

A, b, c


(array([[0.37, 0.94, 0.72, 0.96, 0.34, 0.21, 0.84, 0.95, 0.83, 0.73, 0.96,
         0.13, 0.81, 0.05, 0.44, 0.41, 0.28, 0.45, 0.9 ],
        [0.48, 0.38, 0.66, 0.97, 0.74, 0.93, 0.76, 0.29, 0.3 , 0.18, 0.34,
         0.39, 0.61, 0.9 , 0.23, 0.11, 0.41, 0.78, 0.41],
        [0.01, 0.61, 0.66, 0.55, 0.84, 0.71, 0.95, 0.17, 0.13, 0.74, 0.79,
         0.82, 0.7 , 0.89, 0.52, 0.76, 0.89, 0.13, 0.49],
        [0.87, 0.72, 0.17, 0.4 , 0.07, 0.78, 0.03, 0.08, 0.78, 0.84, 0.61,
         0.63, 0.37, 0.54, 0.81, 0.18, 0.9 , 0.13, 0.67],
        [0.94, 0.18, 0.06, 0.11, 0.64, 0.68, 0.37, 0.16, 0.1 , 0.52, 0.45,
         0.44, 0.34, 0.84, 0.3 , 0.92, 0.94, 0.5 , 0.08],
        [0.  , 0.12, 0.44, 0.8 , 1.  , 0.2 , 0.78, 0.13, 0.79, 0.17, 1.  ,
         0.83, 0.97, 0.27, 0.14, 0.79, 0.63, 0.26, 0.36],
        [0.95, 0.79, 0.12, 0.72, 0.21, 0.39, 0.94, 0.17, 0.4 , 0.12, 0.82,
         0.01, 0.23, 0.56, 0.46, 0.99, 0.22, 0.71, 0.59],
        [0.68, 0.49, 0.65, 0.59, 0.85, 0.05, 0.56, 0.94, 0.05, 0.75, 

In [3]:
def get_model(A, b, c):
    m = pyo.ConcreteModel()

    m.m, m.n = A.shape

    # на всякий случай, возьмем с собой
    m.A = A
    m.b = b
    m.c = c
    
    m.I = range(m.m)
    m.J = range(m.n)
    
    m.x = pyo.Var(m.J, domain=pyo.Binary)
    m.obj = pyo.Objective(expr = sum( c[j] * m.x[j] for j in m.J), sense=pyo.minimize)

    @m.Constraint(m.I)
    def не_меньше(m, i):
        return sum(A[i, j] * m.x[j] for j in m.J) >= b[i]

    return m

m = get_model(A, b, c)
m.pprint()

2 Set Declarations
    x_index : Size=1, Index=None, Ordered=Insertion
        Key  : Dimen : Domain : Size : Members
        None :     1 :    Any :   19 : {0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18}
    не_меньше_index : Size=1, Index=None, Ordered=Insertion
        Key  : Dimen : Domain : Size : Members
        None :     1 :    Any :   12 : {0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11}

1 Var Declarations
    x : Size=19, Index=x_index
        Key : Lower : Value : Upper : Fixed : Stale : Domain
          0 :     0 :  None :     1 : False :  True : Binary
          1 :     0 :  None :     1 : False :  True : Binary
          2 :     0 :  None :     1 : False :  True : Binary
          3 :     0 :  None :     1 : False :  True : Binary
          4 :     0 :  None :     1 : False :  True : Binary
          5 :     0 :  None :     1 : False :  True : Binary
          6 :     0 :  None :     1 : False :  True : Binary
          7 :     0 :  None :     1 : False :  True 

In [4]:
def print_solution(m):
    for v in m.component_data_objects(pyo.Var):
        if v.value and v.value > 0:
            print(str(v), v.value)

In [5]:
solver = pyo.SolverFactory('cbc')
solver.solve(m).write()
print_solution(m)

# ==========================================================
# = Solver Results                                         =
# ==========================================================
# ----------------------------------------------------------
#   Problem Information
# ----------------------------------------------------------
Problem: 
- Name: unknown
  Lower bound: 4.50148447
  Upper bound: 4.50148447
  Number of objectives: 1
  Number of constraints: 12
  Number of variables: 19
  Number of binary variables: 19
  Number of integer variables: 19
  Number of nonzeros: 19
  Sense: minimize
# ----------------------------------------------------------
#   Solver Information
# ----------------------------------------------------------
Solver: 
- Status: ok
  User time: -1.0
  System time: 0.04
  Wallclock time: 0.04
  Termination condition: optimal
  Termination message: Model was solved to optimality (subject to tolerances), and an optimal solution is available.
  Statistics: 
    Branch